<h1> Capstone Project: Battle of the Neighborhoods </h1>

<h2> Introduction/Business Problem </h2>

<b> "Where would you recommend to open an Indian restaurant in New York City?" </b>

The stakeholder wants to open a new Indian restaurant in NYC and asked me this question.
He explains the customer's point of view that the location should be popular and there shouldn't be too many Indian restaurants already present in the vicinity. The Indian restaurant being launched would be a fusion of the different regional cuisines in India so would stand out, so all the attention should be on localities lacking Indian restaurants. Rental price is not a concern to the stakeholder, as well as how good the existing restaurants are as the stakeholder is confident of his food quality.

I need to pick a list of locations suitable for this.



<h2>Data</h2>


Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood.

Luckily, this dataset exists for free on the web. Feel free to try to find this dataset on your own, but here is the link to the dataset: https://geo.nyu.edu/catalog/nyu_2451_34572

In [10]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


<b>Let us load and explore the data</b>

In [11]:
import json
import pandas as pd
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [18]:
#newyork_data


In [13]:
neighborhoods_data = newyork_data['features']

<b>Transforming the data into a Pandas dataframe</b>

In [14]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [15]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
    

In [60]:
neighborhoods.head()
neighborhoods['Borough'].unique()

array(['Bronx', 'Manhattan', 'Brooklyn', 'Queens', 'Staten Island'],
      dtype=object)

In [17]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


<h2> Methodology </h2>

<b> The basic methodology used in this project is as follows:
    1. Each borough's coordinates are found using the geocode library
    2. Using foursqaure library, we find out venues and their locations
    3. We further analyze the data returned to gain insights on our data 

In [19]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    ca-certificates-2019.6.16  |       hecc5488_0         145 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    certifi-2019.6.16          |           py36_1         149 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

<b>After importing the necessary libraries, Geopy library will be used to get the latitude longitude coordinates of NYC. <b>

In [20]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


<b>Let us create a map of NYC with the data above. Folium will be used for this </b>

In [107]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

<h3> Exploring Borough 1: Manhattan </h3>

In [23]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [24]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7900869, -73.9598295.


<b> Foursquare Credentials definition </b>

In [108]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 
CLIENT_SECRET:


In [26]:
# type your answer here
borough_latitude= 40.7900869
borough_longitude= -73.9598295
LIMIT= 100
radius= 500
url= 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,CLIENT_SECRET, VERSION, borough_latitude, borough_longitude, radius, LIMIT)
url


'https://api.foursquare.com/v2/venues/explore?&client_id=GUKELLG0ELPXMASOEGMNYEFZLFZMYBM5Q4CT3KR3RMAD0WVG&client_secret=5L03CBXDYDRKBTEWJWLY13CYA14WJZHNSRK31BKRNE3B4SKH&v=20180605&ll=40.7900869,-73.9598295&radius=500&limit=100'

In [27]:
results = requests.get(url).json()

In [29]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [30]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat  \
0                            North Meadow            Park  40.792027   
1              Central Park Tennis Center    Tennis Court  40.789313   
2                             East Meadow           Field  40.790160   
3  Central Park - North Meadow Fields 1-4  Baseball Field  40.792128   
4       Central Park - Gate Of All Saints            Park  40.791591   

         lng  
0 -73.959853  
1 -73.961862  
2 -73.955498  
3 -73.961362  
4 -73.964795

In [31]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [32]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )


Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [33]:
manhattan_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066      Starbucks   
4  Marble Hill              40.876551               -73.91066        Dunkin'   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877531       -73.905582    Coffee Shop  
4       40.877136       -73.906666     Donut Shop

In [34]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 342 uniques categories.


<b> Analyze each neighborhood in Manhattan </b>

In [35]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Marble Hill                  0               0                  0   
1  Marble Hill                  0               0                  0   
2  Marble Hill                  0               0                  0   
3  Marble Hill                  0               0                  0   
4  Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  BBQ Joint  \
0                      0                    0              0          0   
1                      0                    0              0          0   
2                      0                    0              0          0   
3                      0                    0              0          0   
4                      0                    0              0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Basketball Court  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0                 0                0         0            0           0   
1                 0                0         0            0           0   
2                 0                0         0            0           0   
3                 0                0         0            0           0   
4                 0                0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0                         0          0           0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0           0              0          0         0           0   
1           0              0          0         0           0   
2           0              0          0         0           0   
3           0              0          0         0           0   
4           0              0          0         0           0   

   Brazilian Restaurant  Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  \
0                     0               0         

In [36]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000            0.00               0.00   
1         Carnegie Hill           0.000000            0.00               0.00   
2        Central Harlem           0.000000            0.00               0.00   
3               Chelsea           0.000000            0.00               0.00   
4             Chinatown           0.000000            0.00               0.00   
5          Civic Center           0.000000            0.00               0.00   
6               Clinton           0.000000            0.00               0.00   
7           East Harlem           0.000000            0.00               0.00   
8          East Village           0.000000            0.00               0.00   
9    Financial District           0.010000            0.00               0.00   
10             Flatiron           0.000000            0.00               0.00   
11             Gramercy           0.000000            0.00               0.00   
12    Greenwich Village           0.000000            0.00               0.00   
13     Hamilton Heights           0.000000            0.00               0.00   
14         Hudson Yards           0.000000            0.00               0.00   
15               Inwood           0.000000            0.00               0.00   
16           Lenox Hill           0.000000            0.00               0.01   
17       Lincoln Square           0.000000            0.00               0.00   
18         Little Italy           0.000000            0.00               0.00   
19      Lower East Side           0.000000            0.00               0.00   
20     Manhattan Valley           0.000000            0.00               0.00   
21       Manhattanville           0.000000            0.00               0.00   
22          Marble Hill           0.000000            0.00               0.00   
23              Midtown           0.000000            0.00               0.00   
24        Midtown South           0.000000            0.00               0.00   
25  Morningside Heights           0.000000            0.00               0.00   
26          Murray Hill           0.000000            0.00               0.00   
27                 Noho           0.000000            0.01               0.00   
28     Roosevelt Island           0.000000            0.00               0.00   
29                 Soho           0.010000            0.00               0.00   
30      Stuyvesant Town           0.000000            0.00               0.00   
31         Sutton Place           0.000000            0.01               0.00   
32              Tribeca           0.000000            0.00               0.00   
33           Tudor City           0.000000            0.00               0.00   
34           Turtle Bay           0.000000            0.00               0.00   
35      Upper East Side           0.000000            0.00               0.00   
36      Upper West Side           0.010000            0.00               0.00   
37   Washington Heights           0.011494            0.00               0.00   
38         West Village           0.010000            0.00               0.00   
39            Yorkville           0.000000            0.00               0.00   

    African Restaurant  American Restaurant  Antique Shop  Arcade  \
0             0.000000             0.010101          0.00    0.00   
1             0.000000             0.010000          0.00    0.00   
2             0.071429             0.047619          0.00    0.00   
3             0.000000             0.030000          0.01    0.00   
4             0.000000             0.040000          0.00    0.00   
5             0.000000             0.030000          0.01    0.00   
6             0.000000             0.040000          0.00    0.00   
7             0.000000             0.000000          0.00    0.00   
8             0.000000             0.020000          0.01    0.00   

In [43]:
manhattan_indian= manhattan_grouped[manhattan_grouped['Indian Restaurant']== 0.000000]

In [45]:
manhattan_indian['Neighborhood']

0     Battery Park City
2        Central Harlem
4             Chinatown
6               Clinton
7           East Harlem
8          East Village
11             Gramercy
14         Hudson Yards
15               Inwood
16           Lenox Hill
17       Lincoln Square
18         Little Italy
22          Marble Hill
24        Midtown South
26          Murray Hill
28     Roosevelt Island
29                 Soho
30      Stuyvesant Town
33           Tudor City
35      Upper East Side
38         West Village
Name: Neighborhood, dtype: object

<b> As shown above, in Manhattan any of the above locations can be used to open an Indian Restaurant. </b>

<h2> Exploring Borough 2: Bronx </h2>

In [47]:
bronx_data = neighborhoods[neighborhoods['Borough'] == 'Bronx'].reset_index(drop=True)
bronx_data.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [48]:
address = 'Bronx, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.85048545, -73.8404035580209.


In [49]:
borough_latitude= 40.85048545
borough_longitude= -73.8404035580209
LIMIT= 100
radius= 500
url= 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,CLIENT_SECRET, VERSION, borough_latitude, borough_longitude, radius, LIMIT)
url


'https://api.foursquare.com/v2/venues/explore?&client_id=GUKELLG0ELPXMASOEGMNYEFZLFZMYBM5Q4CT3KR3RMAD0WVG&client_secret=5L03CBXDYDRKBTEWJWLY13CYA14WJZHNSRK31BKRNE3B4SKH&v=20180605&ll=40.85048545,-73.8404035580209&radius=500&limit=100'

In [50]:
results = requests.get(url).json()

In [51]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories  \
0  Residence Inn by Marriott New York The Bronx a...                 Hotel   
1                                         LA Fitness  Gym / Fitness Center   
2                                          Starbucks           Coffee Shop   
3                               Skyline Bar & Lounge                Lounge   
4                             Applebee's Grill + Bar   American Restaurant   

         lat        lng  
0  40.849325 -73.842534  
1  40.849739 -73.841949  
2  40.851371 -73.844087  
3  40.852904 -73.842612  
4  40.848867 -73.842386

In [52]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [71]:
bronx_venues = getNearbyVenues(names=bronx_data['Neighborhood'],
                                   latitudes=bronx_data['Latitude'],
                                   longitudes=bronx_data['Longitude']
                                  )


Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Claremont Village
Concourse Village
Mount Eden
Mount Hope
Bronxdale
Allerton
Kingsbridge Heights


In [54]:
bronx_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896649       -73.844846   
2                         Carvel Ice Cream       40.890487       -73.848568   
3  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
4                                  Dunkin'       40.890459       -73.849089   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2        Ice Cream Shop  
3  Caribbean Restaurant  
4            Donut Shop

In [55]:
print('There are {} uniques categories.'.format(len(bronx_venues['Venue Category'].unique())))

There are 171 uniques categories.


<b> Analyze each neighborhood in Bronx </b>

In [56]:
# one hot encoding
bronx_onehot = pd.get_dummies(bronx_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
bronx_onehot['Neighborhood'] = bronx_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [bronx_onehot.columns[-1]] + list(bronx_onehot.columns[:-1])
bronx_onehot = bronx_onehot[fixed_columns]

bronx_onehot.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0    Wakefield                  0                   0                    0   
1    Wakefield                  0                   0                    0   
2    Wakefield                  0                   0                    0   
3    Wakefield                  0                   0                    0   
4    Wakefield                  0                   0                    0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Asian Restaurant  \
0       0                 0            0           0                 0   
1       0                 0            0           0                 0   
2       0                 0            0           0                 0   
3       0                 0            0           0                 0   
4       0                 0            0           0                 0   

   Athletics & Sports  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                   0          0           0       0     0    0   
1                   0          0           0       0     0    0   
2                   0          0           0       0     0    0   
3                   0          0           0       0     0    0   
4                   0          0           0       0     0    0   

   Baseball Field  Basketball Court  Beer Bar  Boat or Ferry  Bookstore  \
0               0                 0         0              0          0   
1               0                 0         0              0          0   
2               0                 0         0              0          0   
3               0                 0         0              0          0   
4               0                 0         0              0          0   

   Bowling Alley  Breakfast Spot  Brewery  Buffet  Building  Burger Joint  \
0              0               0        0       0         0             0   
1              0               0        0       0         0             0   
2              0               0        0       0         0             0   
3              0               0        0       0         0             0   
4              0               0        0       0         0             0   

   Bus Line  Bus Station  Bus Stop  Café  Camera Store  Candy Store  \
0         0            0         0     0             0            0   
1         0            0         0     0             0            0   
2         0            0         0     0             0            0   
3         0            0         0     0             0            0   
4         0            0         0     0             0            0   

   Caribbean Restaurant  Check Cashing Service  Cheese Shop  \
0                     0                      0            0   
1                     0                      0            0   
2                     0                      0            0   
3                     1                      0            0   
4                     0                      0            0   

   Chinese Restaurant  Clothing Store  Coffee Shop  Comfort Food Restaurant  \
0                   0               0            0                        0   
1                   0               0            0                        0   
2                   0               0            0                        0   
3                   0               0            0                        0   
4                   0               0            0                        0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0                           0                  0               0   
1                           0                  0               0   
2                           0                  0               0   
3                           0                  0               0   
4                           0                  0               0   

   Cupcake Shop  Dance Studio  Deli / Bodega  Department Store  Dessert Shop  \
0

In [57]:
bronx_grouped = bronx_onehot.groupby('Neighborhood').mean().reset_index()
bronx_grouped

Neighborhood  Accessories Store  African Restaurant  \
0              Allerton           0.000000            0.000000   
1            Baychester           0.047619            0.000000   
2          Bedford Park           0.000000            0.000000   
3               Belmont           0.000000            0.000000   
4             Bronxdale           0.000000            0.000000   
5           Castle Hill           0.000000            0.000000   
6           City Island           0.000000            0.000000   
7     Claremont Village           0.000000            0.000000   
8          Clason Point           0.000000            0.000000   
9            Co-op City           0.000000            0.000000   
10            Concourse           0.000000            0.000000   
11    Concourse Village           0.000000            0.000000   
12         Country Club           0.000000            0.000000   
13         East Tremont           0.000000            0.000000   
14          Eastchester           0.000000            0.000000   
15             Edenwald           0.000000            0.000000   
16       Edgewater Park           0.000000            0.000000   
17            Fieldston           0.000000            0.000000   
18              Fordham           0.010989            0.010989   
19         High  Bridge           0.000000            0.000000   
20          Hunts Point           0.000000            0.000000   
21          Kingsbridge           0.000000            0.000000   
22  Kingsbridge Heights           0.000000            0.000000   
23             Longwood           0.000000            0.000000   
24              Melrose           0.000000            0.000000   
25       Morris Heights           0.000000            0.000000   
26          Morris Park           0.000000            0.000000   
27           Morrisania           0.000000            0.000000   
28           Mott Haven           0.000000            0.000000   
29           Mount Eden           0.000000            0.000000   
30           Mount Hope           0.000000            0.000000   
31      North Riverdale           0.000000            0.000000   
32              Norwood           0.000000            0.000000   
33            Olinville           0.000000            0.000000   
34          Parkchester           0.000000            0.000000   
35           Pelham Bay           0.000000            0.000000   
36       Pelham Gardens           0.000000            0.000000   
37       Pelham Parkway           0.000000            0.000000   
38          Port Morris           0.000000            0.000000   
39            Riverdale           0.000000            0.000000   
40        Schuylerville           0.000000            0.000000   
41            Soundview           0.000000            0.000000   
42       Spuyten Duyvil           0.000000            0.000000   
43          Throgs Neck           0.000000            0.000000   
44            Unionport           0.000000            0.000000   
45   University Heights           0.000000            0.040000   
46             Van Nest           0.000000            0.000000   
47            Wakefield           0.000000            0.000000   
48           West Farms           0.000000            0.000000   
49   Westchester Square           0.000000            0.000000   
50       Williamsbridge           0.000000            0.000000   
51             Woodlawn           0.000000            0.000000   

    American Restaurant    Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0              0.000000  0.000000              0.00     0.000000    0.000000   
1              0.047619  0.047619              0.00     0.000000    0.000000   
2              0.000000  0.000000              0.00     0.000000    0.000000   
3              0.010000  0.000000              0.00     0.000000    0.000000   
4              0.000000  0.000000              0.00     0.000000    0.000000   
5              0.000000  0.00000

In [58]:
bronx_indian= bronx_grouped[bronx_grouped['Indian Restaurant']== 0.000000]
bronx_indian['Neighborhood']

0                Allerton
1              Baychester
2            Bedford Park
3                 Belmont
4               Bronxdale
5             Castle Hill
6             City Island
7       Claremont Village
8            Clason Point
9              Co-op City
10              Concourse
12           Country Club
13           East Tremont
14            Eastchester
15               Edenwald
16         Edgewater Park
17              Fieldston
18                Fordham
19           High  Bridge
20            Hunts Point
21            Kingsbridge
22    Kingsbridge Heights
23               Longwood
24                Melrose
25         Morris Heights
26            Morris Park
27             Morrisania
28             Mott Haven
29             Mount Eden
30             Mount Hope
31        North Riverdale
32                Norwood
33              Olinville
34            Parkchester
35             Pelham Bay
36         Pelham Gardens
37         Pelham Parkway
38            Port Morris
39          

<b> As can be seen above, Bronx does not have any Indian restaurants, making it an ideal location to open an Indian Restaurant </b>

<h3> Exploring Borough 3: Brooklyn  </h3>

In [62]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data.head()

Borough Neighborhood   Latitude  Longitude
0  Brooklyn    Bay Ridge  40.625801 -74.030621
1  Brooklyn  Bensonhurst  40.611009 -73.995180
2  Brooklyn  Sunset Park  40.645103 -74.010316
3  Brooklyn   Greenpoint  40.730201 -73.954241
4  Brooklyn    Gravesend  40.595260 -73.973471

In [63]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.6501038, -73.9495823.


In [64]:
borough_latitude= 40.6501038
borough_longitude= -73.9495823
radius= 500
url= 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,CLIENT_SECRET, VERSION, borough_latitude, borough_longitude, radius, LIMIT)
url


'https://api.foursquare.com/v2/venues/explore?&client_id=GUKELLG0ELPXMASOEGMNYEFZLFZMYBM5Q4CT3KR3RMAD0WVG&client_secret=5L03CBXDYDRKBTEWJWLY13CYA14WJZHNSRK31BKRNE3B4SKH&v=20180605&ll=40.6501038,-73.9495823&radius=500&limit=100'

In [65]:
results = requests.get(url).json()

In [66]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name              categories  \
0                              Exquisite Delight    Caribbean Restaurant   
1                                      Jus Juice               Juice Bar   
2                          Nostrand Health Foods               Juice Bar   
3  Courts (Furniture, Electronics, & Appliances)  Furniture / Home Store   
4                                  Tastee Pattee    Caribbean Restaurant   

         lat        lng  
0  40.649091 -73.949243  
1  40.652208 -73.949723  
2  40.649092 -73.949243  
3  40.650529 -73.950617  
4  40.650850 -73.947838

In [69]:
brooklyn_venues = getNearbyVenues(names=brooklyn_data['Neighborhood'],
                                   latitudes=brooklyn_data['Latitude'],
                                   longitudes=brooklyn_data['Longitude']
                                  )


Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


In [70]:
brooklyn_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Bay Ridge              40.625801              -74.030621   
1    Bay Ridge              40.625801              -74.030621   
2    Bay Ridge              40.625801              -74.030621   
3    Bay Ridge              40.625801              -74.030621   
4    Bay Ridge              40.625801              -74.030621   

                         Venue  Venue Latitude  Venue Longitude  \
0  Pilo Arts Day Spa and Salon       40.624748       -74.030591   
1                    Bagel Boy       40.627896       -74.029335   
2                Cocoa Grinder       40.623967       -74.030863   
3                 Pegasus Cafe       40.623168       -74.031186   
4          Ho' Brah Taco Joint       40.622960       -74.031371   

   Venue Category  
0             Spa  
1      Bagel Shop  
2       Juice Bar  
3  Breakfast Spot  
4      Taco Place

In [72]:
print('There are {} uniques categories.'.format(len(brooklyn_venues['Venue Category'].unique())))

There are 286 uniques categories.


<b> Analyze each neighborhood in Brooklyn </b>

In [73]:
# one hot encoding
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhood'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot = brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Yoga Studio  Adult Boutique  Airport Terminal  American Restaurant  \
0            0               0                 0                    0   
1            0               0                 0                    0   
2            0               0                 0                    0   
3            0               0                 0                    0   
4            0               0                 0                    0   

   Antique Shop  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0             0                 0                       0            0   
1             0                 0                       0            0   
2             0                 0                       0            0   
3             0                 0                       0            0   
4             0                 0                       0            0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                   0          0           0       0     0    0   
1                   0          0           1       0     0    0   
2                   0          0           0       0     0    0   
3                   0          0           0       0     0    0   
4                   0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Beach  Beer Bar  \
0               0                 0                 0      0         0   
1               0                 0                 0      0         0   
2               0                 0                 0      0         0   
3               0                 0                 0      0         0   
4               0                 0                 0      0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0           0              0                         0   

   Bike Shop  Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0          0       0           0              0          0         0   
1          0       0           0              0          0         0   
2          0       0           0              0          0         0   
3          0       0           0              0          0         0   
4          0       0           0              0          0         0   

   Boxing Gym  Breakfast Spot  Brewery  Bridge  Bubble Tea Shop  Buffet  \
0           0               0        0       0                0       0   
1           0               0        0       0                0       0   
2           0               0        0       0                0       0   
3           0               1        0       0                0       0   
4           0               0        0       0                0       0   

   Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0             0              0         0            0         0   
1             0              0         0            0         0   
2             0              0         0            0         0   
3             0              0         0            0         0   
4             0              0         0            0         0   

   Business Service  Butcher  Café  Cajun / Creole Restaurant  Candy Store  \
0                 0        0     0                          0            0   
1   

In [74]:
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhood').mean().reset_index()
brooklyn_grouped

Neighborhood  Yoga Studio  Adult Boutique  Airport Terminal  \
0                  Bath Beach     0.000000            0.00          0.000000   
1                   Bay Ridge     0.000000            0.00          0.000000   
2          Bedford Stuyvesant     0.000000            0.00          0.000000   
3                 Bensonhurst     0.000000            0.00          0.000000   
4                Bergen Beach     0.000000            0.00          0.000000   
5                 Boerum Hill     0.023529            0.00          0.000000   
6                Borough Park     0.000000            0.00          0.000000   
7              Brighton Beach     0.000000            0.00          0.000000   
8           Broadway Junction     0.000000            0.00          0.000000   
9            Brooklyn Heights     0.050000            0.00          0.000000   
10                Brownsville     0.000000            0.00          0.045455   
11                   Bushwick     0.000000            0.00          0.000000   
12                   Canarsie     0.000000            0.00          0.000000   
13            Carroll Gardens     0.000000            0.00          0.000000   
14                  City Line     0.000000            0.00          0.000000   
15               Clinton Hill     0.033708            0.00          0.000000   
16                Cobble Hill     0.030000            0.00          0.000000   
17               Coney Island     0.000000            0.00          0.000000   
18              Crown Heights     0.000000            0.00          0.000000   
19              Cypress Hills     0.000000            0.00          0.000000   
20                Ditmas Park     0.018868            0.00          0.000000   
21                   Downtown     0.010000            0.00          0.000000   
22                      Dumbo     0.023810            0.00          0.000000   
23              Dyker Heights     0.000000            0.00          0.000000   
24              East Flatbush     0.000000            0.00          0.000000   
25              East New York     0.000000            0.00          0.000000   
26          East Williamsburg     0.000000            0.00          0.000000   
27                    Erasmus     0.050000            0.00          0.000000   
28                   Flatbush     0.000000            0.00          0.000000   
29                  Flatlands     0.000000            0.00          0.000000   
30                Fort Greene     0.025974            0.00          0.000000   
31              Fort Hamilton     0.000000            0.00          0.000000   
32               Fulton Ferry     0.000000            0.00          0.000000   
33                 Georgetown     0.000000            0.00          0.000000   
34            Gerritsen Beach     0.000000            0.00          0.000000   
35                    Gowanus     0.014706            0.00          0.000000   
36                  Gravesend     0.000000            0.00          0.000000   
37                 Greenpoint     0.030000            0.00          0.000000   
38              Highland Park     0.000000            0.00          0.000000   
39                  Homecrest     0.000000            0.00          0.000000   
40                 Kensington     0.000000            0.00          0.000000   
41                    Madison     0.000000            0.00          0.000000   
42            Manhattan Beach     0.000000            0.00          0.000000   
43          Manhattan Terrace     0.000000            0.00          0.000000   
44                Marine Park     0.000000            0.00          0.000000   
45                    Midwood     0.000000            0.00          0.000000   
46                 Mill Basin     0.000000            0.00          0.000000   
47                Mill Island     0.000000            0.00          0.000000   
48                   New Lots     0.000000            0.00          0.000000   
49               

In [75]:
brooklyn_indian= brooklyn_grouped[brooklyn_grouped['Indian Restaurant']== 0.000000]
brooklyn_indian['Neighborhood']

0              Bath Beach
2      Bedford Stuyvesant
3             Bensonhurst
4            Bergen Beach
6            Borough Park
7          Brighton Beach
8       Broadway Junction
10            Brownsville
12               Canarsie
13        Carroll Gardens
14              City Line
17           Coney Island
18          Crown Heights
19          Cypress Hills
20            Ditmas Park
21               Downtown
22                  Dumbo
23          Dyker Heights
24          East Flatbush
25          East New York
26      East Williamsburg
27                Erasmus
28               Flatbush
29              Flatlands
31          Fort Hamilton
33             Georgetown
34        Gerritsen Beach
36              Gravesend
38          Highland Park
39              Homecrest
40             Kensington
41                Madison
42        Manhattan Beach
43      Manhattan Terrace
44            Marine Park
45                Midwood
46             Mill Basin
47            Mill Island
48          

<b> The above neighborhoods would be suitable to open an Indian Restaurant </b>

<h2> Exploring Borough 4: Queens </h2>

In [78]:
queens_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
queens_data.head()

Borough     Neighborhood   Latitude  Longitude
0  Queens          Astoria  40.768509 -73.915654
1  Queens         Woodside  40.746349 -73.901842
2  Queens  Jackson Heights  40.751981 -73.882821
3  Queens         Elmhurst  40.744049 -73.881656
4  Queens     Howard Beach  40.654225 -73.838138

In [79]:
address = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.6524927, -73.7914214158161.


In [80]:
borough_latitude= 40.6524927
borough_longitude= -73.7914214158161
radius= 500
url= 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,CLIENT_SECRET, VERSION, borough_latitude, borough_longitude, radius, LIMIT)
url


'https://api.foursquare.com/v2/venues/explore?&client_id=GUKELLG0ELPXMASOEGMNYEFZLFZMYBM5Q4CT3KR3RMAD0WVG&client_secret=5L03CBXDYDRKBTEWJWLY13CYA14WJZHNSRK31BKRNE3B4SKH&v=20180605&ll=40.6524927,-73.7914214158161&radius=500&limit=100'

In [81]:
results = requests.get(url).json()

In [82]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat  \
0                       L'Occitane en Provence  Cosmetics Shop  40.650343   
1                                    Starbucks     Coffee Shop  40.650657   
2      American Airlines Flagship First Dining      Restaurant  40.648121   
3  American Airline Flagship The Bridge Lounge  Airport Lounge  40.648424   
4            American Airlines Flagship Lounge  Airport Lounge  40.648101   

         lng  
0 -73.792202  
1 -73.791711  
2 -73.791522  
3 -73.790917  
4 -73.791583

In [83]:
queens_venues = getNearbyVenues(names=queens_data['Neighborhood'],
                                   latitudes=queens_data['Latitude'],
                                   longitudes=queens_data['Longitude']
                                  )


Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


In [84]:
queens_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      Astoria              40.768509              -73.915654   
1      Astoria              40.768509              -73.915654   
2      Astoria              40.768509              -73.915654   
3      Astoria              40.768509              -73.915654   
4      Astoria              40.768509              -73.915654   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0        Favela Grill       40.767348       -73.917897  Brazilian Restaurant  
1     CrossFit Queens       40.769404       -73.918977                   Gym  
2    Titan Foods Inc.       40.769198       -73.919253          Gourmet Shop  
3      Orange Blossom       40.769856       -73.917012          Gourmet Shop  
4  Simply Fit Astoria       40.769114       -73.912403                   Gym

In [85]:
print('There are {} uniques categories.'.format(len(queens_venues['Venue Category'].unique())))

There are 269 uniques categories.


<b> Analyze each neighborhood in Queens </b>

In [86]:
# one hot encoding
queens_onehot = pd.get_dummies(queens_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
queens_onehot['Neighborhood'] = queens_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [queens_onehot.columns[-1]] + list(queens_onehot.columns[:-1])
queens_onehot = queens_onehot[fixed_columns]

queens_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport Terminal  \
0            0                  0                  0                 0   
1            0                  0                  0                 0   
2            0                  0                  0                 0   
3            0                  0                  0                 0   
4            0                  0                  0                 0   

   American Restaurant  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0                    0                 0                       0            0   
1                    0                 0                       0            0   
2                    0                 0                       0            0   
3                    0                 0                       0            0   
4                    0                 0                       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           0                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                   0                0          0           0       0     0   
1                   0                0          0           0       0     0   
2                   0                0          0           0       0     0   
3                   0                0          0           0       0     0   
4                   0                0          0           0       0     0   

   Bar  Baseball Field  Basketball Court  Bath House  Beach  Beach Bar  \
0    0               0                 0           0      0          0   
1    0               0                 0           0      0          0   
2    0               0                 0           0      0          0   
3    0               0                 0           0      0          0   
4    0               0                 0           0      0          0   

   Bed & Breakfast  Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  \
0                0            0           0       0           0          0   
1                0            0           0       0           0          0   
2                0            0           0       0           0          0   
3                0            0           0       0           0          0   
4                0            0           0       0           0          0   

   Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  \
0         0              0                     1               0        0   
1         0              0                     0               0        0   
2         0              0                     0               0        0   
3         0              0                     0               0        0   
4         0              0                     0               0        0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0              0         0   
4                0       0         0             0              0         0   

   Bus Station  Bus Stop  Business Service  Butcher  Café  \
0            0         0                 0        0     0   
1            0         0                 0        0     0   
2            0         0                 0        0     0   
3            0         0       

In [87]:
queens_grouped = queens_onehot.groupby('Neighborhood').mean().reset_index()
queens_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000           0.000000   
1                Astoria     0.000000           0.000000           0.000000   
2        Astoria Heights     0.000000           0.000000           0.000000   
3             Auburndale     0.000000           0.000000           0.000000   
4            Bay Terrace     0.000000           0.025641           0.000000   
5                Bayside     0.014085           0.000000           0.000000   
6              Bayswater     0.000000           0.000000           0.000000   
7             Beechhurst     0.066667           0.000000           0.000000   
8               Bellaire     0.000000           0.000000           0.000000   
9           Belle Harbor     0.000000           0.000000           0.000000   
10             Bellerose     0.000000           0.000000           0.000000   
11            Blissville     0.000000           0.000000           0.000000   
12          Breezy Point     0.000000           0.000000           0.000000   
13             Briarwood     0.000000           0.000000           0.000000   
14         Broad Channel     0.000000           0.000000           0.000000   
15            Brookville     0.000000           0.000000           0.000000   
16       Cambria Heights     0.000000           0.000000           0.000000   
17         College Point     0.000000           0.000000           0.000000   
18                Corona     0.000000           0.000000           0.000000   
19            Douglaston     0.000000           0.000000           0.000000   
20         East Elmhurst     0.000000           0.000000           0.000000   
21              Edgemere     0.000000           0.000000           0.000000   
22              Elmhurst     0.000000           0.000000           0.000000   
23          Far Rockaway     0.000000           0.000000           0.000000   
24           Floral Park     0.000000           0.000000           0.000000   
25              Flushing     0.016949           0.000000           0.000000   
26          Forest Hills     0.051282           0.000000           0.000000   
27  Forest Hills Gardens     0.000000           0.000000           0.000000   
28         Fresh Meadows     0.000000           0.000000           0.000000   
29             Glen Oaks     0.000000           0.000000           0.000000   
30              Glendale     0.000000           0.000000           0.000000   
31               Hammels     0.000000           0.000000           0.000000   
32             Hillcrest     0.000000           0.000000           0.000000   
33                Hollis     0.000000           0.000000           0.000000   
34            Holliswood     0.000000           0.000000           0.000000   
35          Howard Beach     0.000000           0.000000           0.000000   
36         Hunters Point     0.013699           0.000000           0.000000   
37       Jackson Heights     0.000000           0.000000           0.000000   
38        Jamaica Center     0.000000           0.000000           0.000000   
39       Jamaica Estates     0.000000           0.000000           0.000000   
40         Jamaica Hills     0.000000           0.000000           0.000000   
41           Kew Gardens     0.000000           0.000000           0.000000   
42     Kew Gardens Hills     0.000000           0.000000           0.000000   
43             Laurelton     0.000000           0.000000           0.000000   
44           Lefrak City     0.000000           0.000000           0.000000   
45            Lindenwood     0.000000           0.000000           0.000000   
46           Little Neck     0.000000           0.000000           0.000000   
47      Long Island City     0.000000           0.000000           0.000000   
48                 Malba     0.000000           0.000000           0.000000   
49               Maspeth     0.000000           0.000000      

In [88]:
queens_indian= queens_grouped[queens_grouped['Indian Restaurant']== 0.000000]
queens_indian['Neighborhood']

0                  Arverne
2          Astoria Heights
3               Auburndale
4              Bay Terrace
6                Bayswater
7               Beechhurst
8                 Bellaire
9             Belle Harbor
10               Bellerose
11              Blissville
12            Breezy Point
13               Briarwood
14           Broad Channel
15              Brookville
16         Cambria Heights
17           College Point
18                  Corona
19              Douglaston
20           East Elmhurst
21                Edgemere
22                Elmhurst
23            Far Rockaway
25                Flushing
26            Forest Hills
27    Forest Hills Gardens
28           Fresh Meadows
30                Glendale
31                 Hammels
32               Hillcrest
33                  Hollis
34              Holliswood
35            Howard Beach
36           Hunters Point
37         Jackson Heights
38          Jamaica Center
42       Kew Gardens Hills
43               Laurelton
4

<b> As can be seen above, the above neighborhoods are suitable to open an Indian Restaurant </b>

<h2> Exploring Borough 5: Staten Island </h2>

In [90]:
si_data = neighborhoods[neighborhoods['Borough'] == 'Staten Island'].reset_index(drop=True)
si_data.head()

Borough   Neighborhood   Latitude  Longitude
0  Staten Island     St. George  40.644982 -74.079353
1  Staten Island   New Brighton  40.640615 -74.087017
2  Staten Island      Stapleton  40.626928 -74.077902
3  Staten Island       Rosebank  40.615305 -74.069805
4  Staten Island  West Brighton  40.631879 -74.107182

In [91]:
address = 'Staten Island, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.5834557, -74.1496048.


In [92]:
borough_latitude= 40.5834557
borough_longitude= -74.1496048
radius= 500
url= 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,CLIENT_SECRET, VERSION, borough_latitude, borough_longitude, radius, LIMIT)
url


'https://api.foursquare.com/v2/venues/explore?&client_id=GUKELLG0ELPXMASOEGMNYEFZLFZMYBM5Q4CT3KR3RMAD0WVG&client_secret=5L03CBXDYDRKBTEWJWLY13CYA14WJZHNSRK31BKRNE3B4SKH&v=20180605&ll=40.5834557,-74.1496048&radius=500&limit=100'

In [95]:
results = requests.get(url).json()

In [96]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name       categories        lat        lng
0   Greenbelt Nature Center            Trail  40.586616 -74.146917
1                    SUBWAY   Sandwich Place  40.587029 -74.152155
2  Port Richmond Yatch Club  Harbor / Marina  40.584791 -74.153294
3               Decker Farm             Farm  40.583850 -74.154074
4           Greenbelt Trail            Trail  40.586655 -74.147020

In [97]:
si_venues = getNearbyVenues(names=si_data['Neighborhood'],
                                   latitudes=si_data['Latitude'],
                                   longitudes=si_data['Longitude']
                                  )


St. George
New Brighton
Stapleton
Rosebank
West Brighton
Grymes Hill
Todt Hill
South Beach
Port Richmond
Mariner's Harbor
Port Ivory
Castleton Corners
New Springville
Travis
New Dorp
Oakwood
Great Kills
Eltingville
Annadale
Woodrow
Tottenville
Tompkinsville
Silver Lake
Sunnyside
Park Hill
Westerleigh
Graniteville
Arlington
Arrochar
Grasmere
Old Town
Dongan Hills
Midland Beach
Grant City
New Dorp Beach
Bay Terrace
Huguenot
Pleasant Plains
Butler Manor
Charleston
Rossville
Arden Heights
Greenridge
Heartland Village
Chelsea
Bloomfield
Bulls Head
Richmond Town
Shore Acres
Clifton
Concord
Emerson Hill
Randall Manor
Howland Hook
Elm Park
Manor Heights
Willowbrook
Sandy Ground
Egbertville
Prince's Bay
Lighthouse Hill
Richmond Valley
Fox Hills


In [98]:
si_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   St. George              40.644982              -74.079353   
1   St. George              40.644982              -74.079353   
2   St. George              40.644982              -74.079353   
3   St. George              40.644982              -74.079353   
4   St. George              40.644982              -74.079353   

                                 Venue  Venue Latitude  Venue Longitude  \
0                                 Beso       40.643306       -74.076508   
1  Staten Island September 11 Memorial       40.646767       -74.076510   
2        Richmond County Bank Ballpark       40.645056       -74.076864   
3                         A&S Pizzeria       40.643940       -74.077626   
4                   St. George Theatre       40.642253       -74.077496   

        Venue Category  
0     Tapas Restaurant  
1  Monument / Landmark  
2     Baseball Stadium  
3          Pizza Place  
4              Theater

In [99]:
print('There are {} uniques categories.'.format(len(si_venues['Venue Category'].unique())))

There are 176 uniques categories.


<b> Exploring each neighborhood in Staten Island </b>

In [100]:
# one hot encoding
si_onehot = pd.get_dummies(si_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
si_onehot['Neighborhood'] = si_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [si_onehot.columns[-1]] + list(si_onehot.columns[:-1])
si_onehot = si_onehot[fixed_columns]

si_onehot.head()

Neighborhood  American Restaurant  Arcade  Art Gallery  Art Museum  \
0   St. George                    0       0            0           0   
1   St. George                    0       0            0           0   
2   St. George                    0       0            0           0   
3   St. George                    0       0            0           0   
4   St. George                    0       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Automotive Shop  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 1   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Beach  Beer Bar  Big Box Store  Board Shop  Boat or Ferry  Bookstore  \
0      0         0              0           0              0          0   
1      0         0              0           0              0          0   
2      0         0              0           0              0          0   
3      0         0              0           0              0          0   
4      0         0              0           0              0          0   

   Boutique  Bowling Alley  Breakfast Spot  Brewery  Burger Joint  Bus Stop  \
0         0              0               0        0             0         0   
1         0              0               0        0             0         0   
2         0              0               0        0             0         0   
3         0              0               0        0             0         0   
4         0              0               0        0             0         0   

   Business Service  Butcher  Cafeteria  Café  Cajun / Creole Restaurant  \
0                 0        0          0     0                          0   
1                 0        0          0     0                          0   
2                 0        0          0     0                          0   
3                 0        0          0     0                          0   
4                 0        0          0     0                          0   

   Campground  Caribbean Restaurant  Chinese Restaurant  Clothing Store  \
0           0                     0                   0               0   
1           0                     0                   0               0   
2           0                     0                   0               0   
3           0                     0                   0               0   
4           0                     0                   0               0   

   Coffee Shop  Comedy Club  Comfort Food Restaurant  Concert Hall  \
0            0            0                        0             0   
1            0            0                        0             0   
2            0            0                        0             0   
3            0            0                        0             0   
4            0            0                        0             0   

   Convenience Store  Cosmetics Shop  Dance Studio  Deli / Bodega  \
0                  0               0             0              0   
1                  0               0             0              0   
2                  0               0             0              0   
3                  0               0             0              

In [101]:
si_grouped = si_onehot.groupby('Neighborhood').mean().reset_index()
si_grouped

Neighborhood  American Restaurant    Arcade  Art Gallery  Art Museum  \
0            Annadale             0.166667  0.000000     0.000000    0.000000   
1       Arden Heights             0.000000  0.000000     0.000000    0.000000   
2           Arlington             0.250000  0.000000     0.000000    0.000000   
3            Arrochar             0.000000  0.000000     0.000000    0.000000   
4         Bay Terrace             0.000000  0.000000     0.000000    0.000000   
5          Bloomfield             0.000000  0.000000     0.000000    0.000000   
6          Bulls Head             0.023810  0.000000     0.000000    0.000000   
7        Butler Manor             0.000000  0.000000     0.000000    0.000000   
8   Castleton Corners             0.000000  0.000000     0.000000    0.000000   
9          Charleston             0.032258  0.000000     0.000000    0.000000   
10            Chelsea             0.000000  0.000000     0.000000    0.000000   
11            Clifton             0.000000  0.000000     0.000000    0.000000   
12            Concord             0.000000  0.000000     0.000000    0.000000   
13       Dongan Hills             0.000000  0.000000     0.000000    0.000000   
14        Egbertville             0.000000  0.000000     0.000000    0.000000   
15           Elm Park             0.125000  0.000000     0.000000    0.000000   
16        Eltingville             0.000000  0.000000     0.000000    0.000000   
17       Emerson Hill             0.000000  0.000000     0.000000    0.000000   
18          Fox Hills             0.000000  0.000000     0.000000    0.000000   
19       Graniteville             0.000000  0.000000     0.000000    0.000000   
20         Grant City             0.038462  0.000000     0.000000    0.000000   
21           Grasmere             0.000000  0.000000     0.000000    0.000000   
22        Great Kills             0.000000  0.000000     0.000000    0.000000   
23         Greenridge             0.000000  0.000000     0.000000    0.000000   
24        Grymes Hill             0.000000  0.000000     0.000000    0.000000   
25  Heartland Village             0.000000  0.000000     0.000000    0.000000   
26           Huguenot             0.000000  0.000000     0.000000    0.000000   
27    Lighthouse Hill             0.000000  0.000000     0.000000    0.166667   
28      Manor Heights             0.066667  0.000000     0.000000    0.000000   
29   Mariner's Harbor             0.000000  0.000000     0.000000    0.000000   
30      Midland Beach             0.000000  0.000000     0.000000    0.000000   
31       New Brighton             0.000000  0.000000     0.000000    0.000000   
32           New Dorp             0.000000  0.000000     0.000000    0.000000   
33     New Dorp Beach             0.000000  0.000000     0.000000    0.000000   
34    New Springville             0.000000  0.000000     0.000000    0.000000   
35            Oakwood             0.000000  0.000000     0.000000    0.000000   
36           Old Town             0.043478  0.000000     0.000000    0.000000   
37          Park Hill             0.000000  0.000000     0.000000    0.000000   
38    Pleasant Plains             0.000000  0.000000     0.000000    0.000000   
39      Port Richmond             0.000000  0.000000     0.000000    0.000000   
40       Prince's Bay             0.000000  0.000000     0.000000    0.000000   
41      Randall Manor             0.000000  0.000000     0.000000    0.000000   
42      Richmond Town             0.000000  0.000000     0.000000    0.000000   
43    Richmond Valley             0.000000  0.000000     0.000000    0.000000   
44           Rosebank             0.000000  0.000000     0.000000    0.000000   
45          Rossville             0.000000  0.000000     0.000000    0.000000   
46       Sandy Ground             0.000000  0.000000     0.125000    0.000000   
47        Shore Acres             0.000000  0.000000     0.000000    0.000000   
48        Silver Lake             0.2500

In [102]:
si_indian= si_grouped[si_grouped['Indian Restaurant']== 0.000000]
si_indian['Neighborhood']

0              Annadale
1         Arden Heights
2             Arlington
3              Arrochar
4           Bay Terrace
5            Bloomfield
6            Bulls Head
7          Butler Manor
8     Castleton Corners
9            Charleston
10              Chelsea
11              Clifton
12              Concord
13         Dongan Hills
14          Egbertville
15             Elm Park
16          Eltingville
17         Emerson Hill
18            Fox Hills
19         Graniteville
20           Grant City
21             Grasmere
22          Great Kills
23           Greenridge
24          Grymes Hill
25    Heartland Village
26             Huguenot
27      Lighthouse Hill
28        Manor Heights
29     Mariner's Harbor
30        Midland Beach
31         New Brighton
33       New Dorp Beach
34      New Springville
35              Oakwood
36             Old Town
37            Park Hill
38      Pleasant Plains
39        Port Richmond
40         Prince's Bay
41        Randall Manor
42        Richmo

<b> As can be seen above, Staten Island does not have any Indian Restaurants. So it will be suitable to open an Indian Restaurant there. </b>

<h2> Results </h2>

<b> Upon analysis of each Borough in New York, we found that Bronx and Staten Island truly lack in Indian Restaurants and hence will be ideal locations to open a new one. Since there isn't a single Indian Restaurant present in these two boroughs, it is fair to say opening an Indian Restaurant in these boroughs will generate some excitement among the crowd of tourists and inhabitants. 

Moreover, several neighborhoods in Brooklyn, Queens and Manhattan lack Indian Restaurants in the vicinity and can prove to be ideal locations too on further inpection. </b>

<h2> Conclusions </h2>

<b> With the given problem statement, the analysis done produced certain results. With further deeper analysis and constaints, we can further narrow down to an even smaller list of ideal neighborhoods. </b>